In [21]:
from utils.db import dbconn
conn = dbconn('dawndb')
import pandas as pd
pd.options.display.float_format = "{:,.2f}".format
df_rates = pd.read_sql_query("SELECT date, rate FROM rates where name='FED_FUND'",
                             conn,
                             parse_dates=['date'],
                             index_col=['date']).sort_index()
df_balances = pd.read_sql_query("SELECT * FROM strategy_im",
                                conn,
                                parse_dates=['date'],
                                index_col=['date']).sort_index()
df_balances[['broker', 'strategy']] = df_balances[['broker', 'strategy']].astype('category')

In [22]:
from IPython.display import display
from pandas.tseries.offsets import BDay
import numpy as np

def f(df_balances, df_rates, broker, start_date, end_date):
    df = (df_balances[df_balances.broker == broker].
      set_index("strategy", append=True)["amount"].
      unstack("strategy"))
    df[df.isnull()] = 0.
    drange = pd.date_range(pd.Timestamp(start_date) - BDay(), end_date)
    rates = df_rates.reindex(drange, method="ffill") /100 /360
    df = df.reindex(drange, method="ffill")
    if broker in ["BAML_ISDA", "CITI"]:
        d = {}
        for strat in df:
            s = df.loc[start_date:, strat]
            ir_bal = 0.
            for bal, r in zip(s.values, rates.loc[start_date:, 'rate'].values):
                bal += ir_bal
                ir_bal += bal * r
            d[strat] = ir_bal
        result = pd.Series(d, name='amount')
    else:
        result = (df.loc[start_date:] * rates.loc[start_date:].values).sum().to_frame(name='amount')
    display(result)
    print(result.sum())
    
from functools import partial
f_print = partial(f, df_balances, df_rates)

In [24]:
from ipywidgets import widgets, Layout
import datetime
broker_widget = widgets.Dropdown(
    options=df_balances.broker.cat.categories,
    value='CITI',
    description='Broker:',
    disabled=False,
)
start_date = widgets.DatePicker(
    description='start:',
    disabled=False,
    value=datetime.date(2019, 12, 1)
)
end_date = widgets.DatePicker(
    description='end:',
    disabled=False,
    value=datetime.date(2019, 12, 31)
)
output = widgets.interactive_output(f_print, {'broker': broker_widget, 'start_date': start_date, 'end_date': end_date})
output.layout= Layout(margin='auto auto auto 90px')
widgets.VBox([widgets.HBox([broker_widget, start_date, end_date]), output])

In [ ]:
df_balances[df_balances.broker=='GS'].loc["2019-06-10"]

In [23]:
df_gs=df_balances[df_balances.broker == "MS"]
df_gs.groupby(df_gs.index)['amount'].sum()["2019-12-01":]

date
2019-12-02   -8,800,000.00
2019-12-03   -8,800,000.00
2019-12-04   -8,800,000.00
2019-12-05   -8,800,000.00
2019-12-06   -8,800,000.00
2019-12-09   -8,800,000.00
2019-12-10   -8,800,000.00
2019-12-11   -9,070,000.00
2019-12-12   -9,070,000.00
2019-12-13   -9,070,000.00
2019-12-16   -9,070,000.00
2019-12-17   -9,070,000.00
2019-12-18   -9,070,000.00
2019-12-19   -9,070,000.00
2019-12-20   -9,070,000.00
2019-12-23   -9,070,000.00
2019-12-26   -9,070,000.00
2019-12-27   -9,070,000.00
2019-12-30   -9,070,000.00
2020-01-01   -9,070,000.00
2020-01-02   -9,070,000.00
2020-01-03   -9,070,000.00
Name: amount, dtype: float64

In [11]:
def f(df_balances, df_rates, broker, start_date, end_date):
    df = (df_balances[df_balances.broker == broker].
      set_index("strategy", append=True)["amount"].
      unstack("strategy"))
    df[df.isnull()] = 0.
    drange = pd.date_range(pd.Timestamp(start_date) - BDay(), end_date)
    rates = df_rates.reindex(drange, method="ffill") /100 /360
    df = df.reindex(drange, method="ffill")
    if broker in ["BAML_ISDA", "CITI"]:
        d = {}
        for strat in df:
            s = df.loc[start_date:, strat]
            ir_bal = 0.
            for bal, r in zip(s.values, rates.loc[start_date:, 'rate'].values):
                bal += ir_bal
                ir_bal += bal * r
            d[strat] = ir_bal
        result = pd.Series(d, name='amount')
    else:
        result = df.loc[start_date:] * rates.loc[start_date:].values
    return result

In [12]:
f(df_balances, df_rates, "GS", "2019-12-01", "2019-12-31").sum(axis=1)

2019-12-01   -1,217.99
2019-12-02   -1,217.99
2019-12-03   -1,210.18
2019-12-04   -1,210.18
2019-12-05   -1,210.18
2019-12-06   -1,440.10
2019-12-07   -1,440.10
2019-12-08   -1,440.10
2019-12-09   -1,440.10
2019-12-10   -1,440.10
2019-12-11   -1,440.10
2019-12-12   -1,474.54
2019-12-13   -1,474.54
2019-12-14   -1,474.54
2019-12-15   -1,474.54
2019-12-16   -1,484.06
2019-12-17   -1,484.06
2019-12-18   -1,474.54
2019-12-19   -1,474.54
2019-12-20   -1,474.54
2019-12-21   -1,474.54
2019-12-22   -1,474.54
2019-12-23   -1,474.54
2019-12-24   -1,474.54
2019-12-25   -1,474.54
2019-12-26   -1,474.54
2019-12-27   -1,474.54
2019-12-28   -1,474.54
2019-12-29   -1,474.54
2019-12-30   -1,474.54
2019-12-31   -1,474.54
Freq: D, dtype: float64